In [200]:
import os
import xml.etree.ElementTree as ET
import json

In [201]:
# Set folder path for processing
target = "/mnt/resources/woolworths/raw_data/AustralianSupermarkets.xml"
output_folder = "data/processed_files/xml_output/"

In [202]:
tree = ET.parse(target)
root = tree.getroot()

In [203]:
name=[]
content={}
def explore(root, name: list, content):
  if root.tag=="ProcessGroup":
    name.append(root.attrib["Name"])
  for process_group_items in root.findall("ProcessGroupItems"):
    for item in process_group_items:
      if item.tag=="ProcessGroup":
        explore(item, name, content)
        name.pop()
      elif item.tag=="Process":
        name.append(item.attrib["Name"])
        key=" --- ".join(name)
        section_id=item.attrib['Id']
        group=item.attrib['Group']
        page_content=key
        page_content+=f"\n\nName: {item.attrib['Name']}"
        page_content+=f"\nObjective: {item.attrib['Objective']}"
        page_content+=f"\ID: {section_id}"
        page_content+=f"\nGroup: {group}"
        for line in item.iter():
          if line.tag=="Text" or line.tag=="Attachment":
            page_content+="\n"+str(line.text)
        content[key]= (section_id, group, page_content)
        name.pop()
      else:
        print(item.tag)


explore(root, name, content)

In [204]:
content

{'AustralianSupermarkets --- Bakery --- Code Control --- Action Markdowns': ('4296',
  'Code Control',
  'AustralianSupermarkets --- Bakery --- Code Control --- Action Markdowns\n\nName: Action Markdowns\nObjective: Provide information on completing markdowns via the RF device and generating reporting to review\\ID: 4296\nGroup: Code Control\nMarkdown Resources\nOur Routine \nhttps://sites.google.com/woolworths.com.au/ourdaysconsistentlygoodchecks/home\nMarkdown Protocols - All Departments\nMarkdown Matrix -Timings Per Department\nMETRO Markdown Matrix\nGrocery and Fresh Convenience Out of Code Guide\nGuide to using Quick Sale Labels\nIf the Quick Sale label looks faded, there is a reference guide to explain the printer cleaning with alcohol swabs.\nIf the label looks pixelated, please raise an incident using the It Service Hub or Service Now app and provide the printer’s serial number located on the back of the device.\nPortable printer cleaning reference guide\nIf the label does not 

In [205]:
i=0
# d={}
for key, value in content.items():
    filename=key.replace(" --- ", "-").replace("/", "")
    filepath = os.path.join(output_folder, filename)
    
    section_id, group, page_content = value
    with open(filepath+".txt", "w") as f:
        f.write(page_content)
    filename, *mid, section_name = key.split(" --- ")

    
    # k=len(key.split(" --- "))
    # if k==6:
    #     print(key)
    # d[k]=d.get(k, 0)+1


    metadata_dict = {
        "group_name":"se",
        "file_type":"section",
        "section_number":section_id,
        "group":group,
        "document_name":mid[0] if len(mid)>0 else "",
        "section_name":section_name,
        "filename":filename,
        "chunk_number":"0",
    }
    with open(filepath+"_metadata.json", "w") as f:
        json.dump(metadata_dict, f)
    i+=1

print(f"Files created: {i}")
    

Files created: 948


In [206]:
len(content)

948

In [188]:
for k, v in sorted(d.items()):
    print(k, v)

2 1
3 53
4 478
5 279
6 114
7 11
8 12
